In [44]:
import tensorflow as tf
# mnist = tf.keras.datasets.mnist

# (x_train, y_train),(x_test, y_test) = mnist.load_data()
# x_train, x_test = x_train / 255.0, x_test / 255.0

In [45]:
# print(y_test)

In [46]:
resource_path = "./resource/abccodes/"

In [47]:
with open(resource_path + "res.txt", 'r') as file:
    abc_codes = file.readlines()

In [48]:
abc_codes

['X: 1\n',
 'K:A\n',
 '"A"ecccf\n',
 '"A"ecccf\n',
 '"A"ecccf\n',
 '"Bm"BcB\n',
 '"E7"Bf\n',
 '"A"ecccf\n',
 '"A"eccccd\n',
 '"D"efe\n',
 '"E7"dcB\n',
 '"A"Acea\n',
 '"A"Aceag=g\n',
 'K:D\n',
 '"D"ffFdd\n',
 '"D"AFAfef\n',
 '"G"ggecd\n',
 '"Em"efd\n',
 '"A7"cBA\n',
 '"D"f^efdcd\n',
 '"D"AFAf=ef\n',
 '"G"gfg\n',
 '"A7"ABc\n',
 '"D"dde\n',
 '"D"dd\n',
 'X: 2\n',
 'K:G\n',
 '"G"ggB^AB\n',
 '"Em"GAB\n',
 '"Am"AA\n',
 '"D7"ABc\n',
 '"G"BAG\n',
 '"G"ggB^AB\n',
 '"Em"GAB\n',
 '"Am"AG\n',
 '"D7"FGA\n',
 '"G"G\n',
 '"D7"A^GADFA\n',
 '"G"B^ABG\n',
 '"A7"^c=c^cAce\n',
 '"D7"fefdef\n',
 '"G"ggde=f\n',
 '"E7"eeBcd\n',
 '"Am"cc\n',
 '"D7"Adc\n',
 '"G"BAG\n',
 '"G"BAGF\n',
 '"Em"EEGG\n',
 '"Am"cA\n',
 '"B7"FBA\n',
 '"Em"GFE\n',
 '"Em"EFG\n',
 '"Am"ABc\n',
 '"B7"B^c^d\n',
 '"Em"ee\n',
 '"F#7"fffe\n',
 '"B7"^defBAF\n',
 '"Em"EEGG\n',
 '"Am"cA\n',
 '"B7"FBA\n',
 '"Em"GFE\n',
 '"Em"EFG\n',
 '"Am"ABc\n',
 '"B7"B^c^d\n',
 '"Em"ee\n',
 '"F#7"fe\n',
 '"B7"^def\n',
 '"Em"e\n',
 '"D7"d\n',
 '"Em"e\n',
 '"E7"e\

In [80]:
# 코드파일 내 존재 음계 종류
keys_list = []
for i in abc_codes:
    if(i[0:2] == 'K:'):
        i = i.replace('K:', '')
        if(i not in keys_list):
            keys_list.append(i)
print(keys_list)

['A\n', 'D\n', 'G\n', 'F\n', 'Em\n', 'C\n', 'Am\n', 'Dm\n', 'Bb\n', 'Bm\n', 'Gm\n', 'E\n', 'B\n', 'Cm\n']


In [85]:
scales = ['C', 'Am']
shap_scales = {'G' : ['f'], 'Em' : ['f'], 'D' : ['c', 'f'], 'Bm' : ['c', 'f'], 'A' : ['c', 'f', 'g'], 'E' : ['c', 'f', 'g', 'd'],
               'B' : ['c', 'f', 'g', 'd', 'a']}
flat_scales = {'F': ['b'], 'Dm' : ['b'], 'Bb' : ['b', 'e'], 'Gm' : ['b', 'e'], 'Cm' : ['b', 'e', 'a']}
# codes = ['"C"', '"C#"', '"D"', '"D#"', '"E"', '"F"', '"F#"', '"G"', '"G#"', '"A"', '"A#"', '"B"',
#           '"Cm"', '"C#m"', '"Dm"', '"D#m"', '"Em"', '"Fm"', '"F#m"', '"Gm"', '"G#m"', '"Am"', '"A#m"', '"Bm"',
#           '"C7"', '"C#7"', '"D7"', '"D#7"', '"E7"', '"F7"', '"F#7"', '"G7"', '"G#7"', '"A7"', '"A#7"', '"B7"']
codes = ['"C"', '"Cm"', '"C7"', '"C#"', '"C#m"', '"C#7"', '"D"', '"Dm"', '"D7"', '"D#"', '"D#m"', '"D#7"',
         '"E"', '"Em"', '"E7"', '"F"', '"Fm"', '"F7"', '"F#"', '"F#m"', '"F#7"', '"G"', '"Gm"', '"G7"',
         '"G#"', '"G#m"', '"G#7"', '"A"', '"Am"', '"A7"', '"A#"', '"A#m"', '"A#7"', '"B"', '"Bm"', '"B7"']
# keys = ['c', '=c', '_c', '^c',
#         'd', '=d', '_d', '^d',
#         'e', '=e', '_e', '^e',
#         'f', '=f', '_f', '^f',
#         'g', '=g', '_g', '^g',
#         'a', '=a', '_a', '^a',
#         'b', '=b', '_b', '^b']
key_nums = {'c' : 0, '_c' : 11, '^c' : 1, 'd' : 2, '_d' : 1, '^d' : 3, 'e' : 4, '_e' : 3, '^e' : 5,
            'f' : 5, '_f' : 4, '^f' : 6, 'g' : 7, '_g' : 6, '^g' : 8, 'a' : 9, '_a' : 8, '^a' : 10,
            'b' : 11, '_b' : 10, '^b' : 0}

In [82]:
x_train = open(resource_path + "x_train.txt", mode='wt', encoding='utf-8')
y_train = open(resource_path + "y_train.txt", mode='wt', encoding='utf-8')
boolean = False
for i in abc_codes:
    # 공백 제거
    i = i.replace('\n', '')
    # 제목이나 음계를 나타내는 경우 패스
    if(i[0:2] == 'X:'):
        print(i)
    # 음게의 경우
    elif(i[0:2] == 'K:'):
        for j in scales:
            if(i[2:] == j):
                key_sig = 'none'
        for key, value in shap_scales.items():
            if(i[2:] == key):
                key_sig = 'shap'
                key_val = value
        for key, value in flat_scales.items():
            if(i[2:] == key):
                key_sig = 'flat'
                key_val = value
        print("음계 : ", i, key_val)
    # 코드의 경우
    else:
        # key_code_list = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
        for j in codes:
            if(j in i):
                print("코드 : ", codes.index(j))
                y_train.write(str(codes.index(j)))
                y_train.write('\n')
                # 코드를 삭제함
                i = i.replace(j, '')
                # 코드를 따로 분리
                # key_code_list[codes.index(j)] = 1
                # 남은 음이름들은 소문자로 모두 변환
                i = i.lower()
        # print("코드 벡터 : ", key_code_list)
        # 빈 리스트 생성
        key_list = []
        # 음이름들을 한글자씩 돌며
        for j in range(len(i)):
            if(boolean):
                boolean = False
                continue
            # 조표가 붙은 경우 2개씩
            if(i[j] == '=' or i[j] == '_' or i[j] == '^'):
                key_list.append(i[j:j+2])
                boolean = True
            # 아닌 경우 하나씩
            else:
                key_list.append(i[j])
        # 분리시킨 음이름
        for j in range(len(key_list)):
            # 음계에 해당하는 음이 있다면 부호를 붙여줌
            if(key_sig != 'none'):
                for k in key_val:
                    if(key_list[j] == k):
                        if(key_sig == 'shap'):
                            key_list[j] = '^' + key_list[j]
                        else:
                            key_list[j] = '_' + key_list[j]
        for j in range(len(key_list)):
            if(key_list[j][0] == '='):
                key_list[j] = key_list[j].replace('=', '')
        print("멜로디 : ", key_list)
        key_num_list = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
        for j in range(len(key_list)):
            for key, value in key_nums.items():
                if(key_list[j] == key):
                    key_num_list[value] = key_num_list[value] + 1
        print("멜로디 벡터 : ", key_num_list)
        for j in range(len(key_num_list)):
            x_train.write(str(key_num_list[j]))
            if (j == len(key_num_list) - 1):
                x_train.write('\n')
            else:
                x_train.write(', ')
x_train.close()
y_train.close()

X: 1
음계 :  K:A ['c', 'f', 'g']
코드 :  27
ecccf
멜로디 :  ['e', '^c', '^c', '^c', '^f']
멜로디 벡터 :  [0, 3, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0]
코드 :  27
ecccf
멜로디 :  ['e', '^c', '^c', '^c', '^f']
멜로디 벡터 :  [0, 3, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0]
코드 :  27
ecccf
멜로디 :  ['e', '^c', '^c', '^c', '^f']
멜로디 벡터 :  [0, 3, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0]
코드 :  34
bcb
멜로디 :  ['b', '^c', 'b']
멜로디 벡터 :  [0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2]
코드 :  14
bf
멜로디 :  ['b', '^f']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1]
코드 :  27
ecccf
멜로디 :  ['e', '^c', '^c', '^c', '^f']
멜로디 벡터 :  [0, 3, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0]
코드 :  27
eccccd
멜로디 :  ['e', '^c', '^c', '^c', '^c', 'd']
멜로디 벡터 :  [0, 4, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  6
efe
멜로디 :  ['e', '^f', 'e']
멜로디 벡터 :  [0, 0, 0, 0, 2, 0, 1, 0, 0, 0, 0, 0]
코드 :  14
dcb
멜로디 :  ['d', '^c', 'b']
멜로디 벡터 :  [0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1]
코드 :  27
acea
멜로디 :  ['a', '^c', 'e', 'a']
멜로디 벡터 :  [0, 1, 0, 0, 1, 0, 0, 0, 0, 2, 0, 0]
코드 :  27
aceag=g
멜로디 :  ['a', '^c', 'e', 'a', '^g

코드 :  21
aggg
멜로디 :  ['a', 'g', 'g', 'g']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 3, 0, 1, 0, 0]
코드 :  8
fffef
멜로디 :  ['^f', '^f', '^f', 'e', '^f']
멜로디 벡터 :  [0, 0, 0, 0, 1, 0, 4, 0, 0, 0, 0, 0]
코드 :  21
ag
멜로디 :  ['a', 'g']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0]
코드 :  8
gfe
멜로디 :  ['g', '^f', 'e']
멜로디 벡터 :  [0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 0, 0]
코드 :  21
dbbaf
멜로디 :  ['d', 'b', 'b', 'a', '^f']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 2]
코드 :  21
aggg
멜로디 :  ['a', 'g', 'g', 'g']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 3, 0, 1, 0, 0]
코드 :  8
fffef
멜로디 :  ['^f', '^f', '^f', 'e', '^f']
멜로디 벡터 :  [0, 0, 0, 0, 1, 0, 4, 0, 0, 0, 0, 0]
코드 :  21
agfg
멜로디 :  ['a', 'g', '^f', 'g']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 1, 2, 0, 1, 0, 0]
코드 :  21
gfgbge
멜로디 :  ['g', '^f', 'g', 'b', 'g', 'e']
멜로디 벡터 :  [0, 0, 0, 0, 1, 0, 1, 3, 0, 0, 0, 1]
코드 :  8
dddef
멜로디 :  ['d', 'd', 'd', 'e', '^f']
멜로디 벡터 :  [0, 0, 3, 0, 1, 0, 1, 0, 0, 0, 0, 0]
코드 :  21
gfgbge
멜로디 :  ['g', '^f', 'g', 'b', 'g', 'e']
멜로디 벡터 :  [0, 0, 0, 0, 1, 0,

멜로디 벡터 :  [1, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 0]
코드 :  6
aacga
멜로디 :  ['a', 'a', 'c', 'g', 'a']
멜로디 벡터 :  [1, 0, 0, 0, 0, 0, 0, 1, 0, 3, 0, 0]
코드 :  6
fae
멜로디 :  ['^f', 'a', 'e']
멜로디 벡터 :  [0, 0, 0, 0, 1, 0, 1, 0, 0, 1, 0, 0]
코드 :  8
d^cde=c
멜로디 :  ['d', '^c', 'd', 'e', 'c']
멜로디 벡터 :  [1, 1, 2, 0, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  21
bdgbd
멜로디 :  ['b', 'd', 'g', 'b', 'd']
멜로디 벡터 :  [0, 0, 2, 0, 0, 0, 0, 1, 0, 0, 0, 2]
코드 :  21
ggbfg
멜로디 :  ['g', 'g', 'b', '^f', 'g']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 1, 3, 0, 0, 0, 1]
코드 :  21
dgbdbg
멜로디 :  ['d', 'g', 'b', 'd', 'b', 'g']
멜로디 벡터 :  [0, 0, 2, 0, 0, 0, 0, 2, 0, 0, 0, 2]
코드 :  0
ecae
멜로디 :  ['e', 'c', 'a', 'e']
멜로디 벡터 :  [1, 0, 0, 0, 2, 0, 0, 0, 0, 1, 0, 0]
코드 :  0
ecgegc
멜로디 :  ['e', 'c', 'g', 'e', 'g', 'c']
멜로디 벡터 :  [2, 0, 0, 0, 2, 0, 0, 2, 0, 0, 0, 0]
코드 :  21
gdbgbd
멜로디 :  ['g', 'd', 'b', 'g', 'b', 'd']
멜로디 벡터 :  [0, 0, 2, 0, 0, 0, 0, 2, 0, 0, 0, 2]
코드 :  8
fed^cdf
멜로디 :  ['^f', 'e', 'd', '^c', 'd', '^f']
멜로디 벡터 :  [0, 1, 2, 0, 1, 0, 2, 0, 0, 0, 

eaaabd
멜로디 :  ['e', 'a', 'a', 'a', 'b', 'd']
멜로디 벡터 :  [0, 0, 1, 0, 1, 0, 0, 0, 0, 3, 0, 1]
코드 :  28
ede
멜로디 :  ['e', 'd', 'e']
멜로디 벡터 :  [0, 0, 1, 0, 2, 0, 0, 0, 0, 0, 0, 0]
코드 :  13
ag
멜로디 :  ['a', 'g']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0]
코드 :  28
edc
멜로디 :  ['e', 'd', 'c']
멜로디 벡터 :  [1, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  13
bcd
멜로디 :  ['b', 'c', 'd']
멜로디 벡터 :  [1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1]
코드 :  28
ecaa
멜로디 :  ['e', 'c', 'a', 'a']
멜로디 벡터 :  [1, 0, 0, 0, 1, 0, 0, 0, 0, 2, 0, 0]
코드 :  13
gefga
멜로디 :  ['g', 'e', '^f', 'g', 'a']
멜로디 벡터 :  [0, 0, 0, 0, 1, 0, 1, 2, 0, 1, 0, 0]
코드 :  13
gef
멜로디 :  ['g', 'e', '^f']
멜로디 벡터 :  [0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 0, 0]
코드 :  8
gdc
멜로디 :  ['g', 'd', 'c']
멜로디 벡터 :  [1, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0]
코드 :  21
bggdgg
멜로디 :  ['b', 'g', 'g', 'd', 'g', 'g']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 0, 4, 0, 0, 0, 1]
코드 :  13
gefga
멜로디 :  ['g', 'e', '^f', 'g', 'a']
멜로디 벡터 :  [0, 0, 0, 0, 1, 0, 1, 2, 0, 1, 0, 0]
코드 :  8
gef
멜로디 :  ['g', 'e', '^f'

코드 :  13
geee
멜로디 :  ['g', 'e', 'e', 'e']
멜로디 벡터 :  [0, 0, 0, 0, 3, 0, 0, 1, 0, 0, 0, 0]
코드 :  13

멜로디 :  []
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
코드 :  8
c
멜로디 :  ['c']
멜로디 벡터 :  [1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
코드 :  21
bdgbgd
멜로디 :  ['b', 'd', 'g', 'b', 'g', 'd']
멜로디 벡터 :  [0, 0, 2, 0, 0, 0, 0, 2, 0, 0, 0, 2]
코드 :  8
cdfafd
멜로디 :  ['c', 'd', '^f', 'a', '^f', 'd']
멜로디 벡터 :  [1, 0, 2, 0, 0, 0, 2, 0, 0, 1, 0, 0]
코드 :  21
bdgbgd
멜로디 :  ['b', 'd', 'g', 'b', 'g', 'd']
멜로디 벡터 :  [0, 0, 2, 0, 0, 0, 0, 2, 0, 0, 0, 2]
코드 :  13
d
멜로디 :  ['d']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0]
코드 :  8
c
멜로디 :  ['c']
멜로디 벡터 :  [1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
코드 :  21
bdgbgd
멜로디 :  ['b', 'd', 'g', 'b', 'g', 'd']
멜로디 벡터 :  [0, 0, 2, 0, 0, 0, 0, 2, 0, 0, 0, 2]
코드 :  8
cdfafd
멜로디 :  ['c', 'd', '^f', 'a', '^f', 'd']
멜로디 벡터 :  [1, 0, 2, 0, 0, 0, 2, 0, 0, 1, 0, 0]
코드 :  21
gdbg
멜로디 :  ['g', 'd', 'b', 'g']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 0, 2, 0, 0, 0, 1]
X: 44
음계 :  K:C ['f']
코드 :  0
g^fgag


...

코드 :  21
babc
멜로디 :  ['b', 'a', 'b', '^c']
멜로디 벡터 :  [0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 2]
코드 :  6
def
멜로디 :  ['d', 'e', '^f']
멜로디 벡터 :  [0, 0, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0]
코드 :  21
gfeg
멜로디 :  ['g', '^f', 'e', 'g']
멜로디 벡터 :  [0, 0, 0, 0, 1, 0, 1, 2, 0, 0, 0, 0]
코드 :  6
fedf
멜로디 :  ['^f', 'e', 'd', '^f']
멜로디 벡터 :  [0, 0, 1, 0, 1, 0, 2, 0, 0, 0, 0, 0]
코드 :  12
edcd
멜로디 :  ['e', 'd', '^c', 'd']
멜로디 벡터 :  [0, 1, 2, 0, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  27
e
멜로디 :  ['e']
멜로디 벡터 :  [0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  27
edce
멜로디 :  ['e', 'd', '^c', 'e']
멜로디 벡터 :  [0, 1, 1, 0, 2, 0, 0, 0, 0, 0, 0, 0]
코드 :  6
d
멜로디 :  ['d']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0]
X: 6
음계 :  K:G ['f']
코드 :  21
ga
멜로디 :  ['g', 'a']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0]
코드 :  6
gf
멜로디 :  ['g', '^f']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0]
코드 :  21
gde
멜로디 :  ['g', 'd', 'e']
멜로디 벡터 :  [0, 0, 1, 0, 1, 0, 0, 1, 0, 0, 0, 0]
코드 :  0
dc
멜로디 :  ['d', 'c']
멜로디 벡터 :  [1, 0, 1, 0, 0, 0, 0, 0, 0, 0

멜로디 :  ['d', 'b', 'e', 'c', 'f', 'd']
멜로디 벡터 :  [1, 0, 2, 0, 1, 1, 0, 0, 0, 0, 0, 1]
코드 :  0
ec
멜로디 :  ['e', 'c']
멜로디 벡터 :  [1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  15
aef
멜로디 :  ['a', 'e', 'f']
멜로디 벡터 :  [0, 0, 0, 0, 1, 1, 0, 0, 0, 1, 0, 0]
코드 :  0
ged
멜로디 :  ['g', 'e', 'd']
멜로디 벡터 :  [0, 0, 1, 0, 1, 0, 0, 1, 0, 0, 0, 0]
코드 :  6
cae
멜로디 :  ['c', 'a', 'e']
멜로디 벡터 :  [1, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0]
코드 :  21
ded
멜로디 :  ['d', 'e', 'd']
멜로디 벡터 :  [0, 0, 2, 0, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  0
cc
멜로디 :  ['c', 'c']
멜로디 벡터 :  [2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
코드 :  21
dca
멜로디 :  ['d', 'c', 'a']
멜로디 벡터 :  [1, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0]
코드 :  0
gce
멜로디 :  ['g', 'c', 'e']
멜로디 벡터 :  [1, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0]
코드 :  21
dag
멜로디 :  ['d', 'a', 'g']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 0, 1, 0, 1, 0, 0]
코드 :  2
egc
멜로디 :  ['e', 'g', 'c']
멜로디 벡터 :  [1, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0]
코드 :  15
dfe
멜로디 :  ['d', 'f', 'e']
멜로디 벡터 :  [0, 0, 1, 0, 1, 1, 0, 0, 0, 0, 0, 0]
코드 :  21
dab
멜로디 :  

멜로디 벡터 :  [0, 0, 0, 1, 0, 0, 1, 0, 0, 1, 0, 1]
코드 :  27
gf
멜로디 :  ['^g', '^f']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0]
코드 :  35
e^d
멜로디 :  ['e', '^d']
멜로디 벡터 :  [0, 0, 0, 1, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  12
eeee
멜로디 :  ['e', 'e', 'e', 'e']
멜로디 벡터 :  [0, 0, 0, 0, 4, 0, 0, 0, 0, 0, 0, 0]
코드 :  27
aaag
멜로디 :  ['a', 'a', 'a', '^g']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 0, 1, 3, 0, 0]
코드 :  6
fffe
멜로디 :  ['^f', '^f', '^f', 'e']
멜로디 벡터 :  [0, 0, 0, 0, 1, 0, 3, 0, 0, 0, 0, 0]
코드 :  27
ceac
멜로디 :  ['^c', 'e', 'a', '^c']
멜로디 벡터 :  [0, 2, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0]
코드 :  12
bee
멜로디 :  ['b', 'e', 'e']
멜로디 벡터 :  [0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 1]
코드 :  27
aaag
멜로디 :  ['a', 'a', 'a', '^g']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 0, 1, 3, 0, 0]
코드 :  19
fffc
멜로디 :  ['^f', '^f', '^f', '^c']
멜로디 벡터 :  [0, 1, 0, 0, 0, 0, 3, 0, 0, 0, 0, 0]
코드 :  34
ba
멜로디 :  ['b', 'a']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1]
코드 :  12
bc
멜로디 :  ['b', '^c']
멜로디 벡터 :  [0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1]
코드 :  27
aaaa

멜로디 벡터 :  [0, 0, 0, 0, 2, 0, 0, 0, 0, 2, 0, 0]
코드 :  6
fedc
멜로디 :  ['^f', 'e', 'd', '^c']
멜로디 벡터 :  [0, 1, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0]
코드 :  12
bdcb
멜로디 :  ['b', 'd', '^c', 'b']
멜로디 벡터 :  [0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 2]
코드 :  27
ae
멜로디 :  ['a', 'e']
멜로디 벡터 :  [0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0]
코드 :  12
bd
멜로디 :  ['b', 'd']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1]
코드 :  27
ce
멜로디 :  ['^c', 'e']
멜로디 벡터 :  [0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  34
dc
멜로디 :  ['d', '^c']
멜로디 벡터 :  [0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0]
코드 :  12
bc
멜로디 :  ['b', '^c']
멜로디 벡터 :  [0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1]
코드 :  27
ce
멜로디 :  ['^c', 'e']
멜로디 벡터 :  [0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  6
df
멜로디 :  ['d', '^f']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0]
코드 :  27
ed
멜로디 :  ['e', 'd']
멜로디 벡터 :  [0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  12
ce
멜로디 :  ['^c', 'e']
멜로디 벡터 :  [0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  27
ecae
멜로디 :  ['e', '^c', 'a', 'e']
멜로디 벡터 :  [0, 1, 0, 0, 2, 0, 0, 

bd
멜로디 :  ['b', 'd']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1]
코드 :  27
cdeae
멜로디 :  ['c', 'd', 'e', 'a', 'e']
멜로디 벡터 :  [1, 0, 1, 0, 2, 0, 0, 0, 0, 1, 0, 0]
코드 :  6
aad
멜로디 :  ['a', 'a', 'd']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 0, 0, 0, 2, 0, 0]
코드 :  13
beg
멜로디 :  ['b', 'e', 'g']
멜로디 벡터 :  [0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 1]
코드 :  27
aa
멜로디 :  ['a', 'a']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0]
코드 :  6
ddd
멜로디 :  ['d', 'd', 'd']
멜로디 벡터 :  [0, 0, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0]
X: 45
음계 :  K:D ['c', 'f']
코드 :  6
fddcdd
멜로디 :  ['^f', 'd', 'd', '^c', 'd', 'd']
멜로디 벡터 :  [0, 1, 4, 0, 0, 0, 1, 0, 0, 0, 0, 0]
코드 :  21
bdd
멜로디 :  ['b', 'd', 'd']
멜로디 벡터 :  [0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 1]
코드 :  27
ace
멜로디 :  ['a', '^c', 'e']
멜로디 벡터 :  [0, 1, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0]
코드 :  6
fddcdd
멜로디 :  ['^f', 'd', 'd', '^c', 'd', 'd']
멜로디 벡터 :  [0, 1, 4, 0, 0, 0, 1, 0, 0, 0, 0, 0]
코드 :  13
bee
멜로디 :  ['b', 'e', 'e']
멜로디 벡터 :  [0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 1]
코드 :  27
ede
멜로디 :  ['e', 'd', '

In [88]:
cons = ''
x_train = open(resource_path + "x_train_x.txt", mode='wt', encoding='utf-8')
y_train = open(resource_path + "y_train_x.txt", mode='wt', encoding='utf-8')
for i in abc_codes:
    # 공백 제거
    i = i.replace('\n', '')
    # 제목이나 음계를 나타내는 경우 패스
    if(i[0:2] == 'X:'):
        pass
    # 음계의 경우
    elif(i[0:2] == 'K:'):
        if(i[2:] == 'G'):
                cons = 'G'
        for j in scales:
            if(i[2:] == j):
                key_sig = 'none'
        for key, value in shap_scales.items():
            if(i[2:] == key):
                key_sig = 'shap'
                key_val = value
        for key, value in flat_scales.items():
            if(i[2:] == key):
                key_sig = 'flat'
                key_val = value
        print("음계 : ", i, key_val)
    # 코드의 경우
    else:
        if(cons == 'G'):
            # key_code_list = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
            for j in codes:
                if(j in i):
                    print("코드 : ", codes.index(j))
                    y_train.write(str(codes.index(j)))
                    y_train.write('\n')
                    # 코드를 삭제함
                    i = i.replace(j, '')
                    # 코드를 따로 분리
                    # key_code_list[codes.index(j)] = 1
                    # 남은 음이름들은 소문자로 모두 변환
                    i = i.lower()
            # print("코드 벡터 : ", key_code_list)
            # 빈 리스트 생성
            key_list = []
            # 음이름들을 한글자씩 돌며
            for j in range(len(i)):
                # 조표가 붙은 경우 2개씩
                if(i[j] == '=' or i[j] == '_' or i[j] == '^'):
                    key_list.append(i[j:j+2])
                    j = j+1
                # 아닌 경우 하나씩
                else:
                    key_list.append(i[j])
            # 분리시킨 음이름
            for j in range(len(key_list)):
                # 음계에 해당하는 음이 있다면 부호를 붙여줌
                for k in key_val:
                    if(key_list[j] == k):
                        if(key_sig == 'shap'):
                            key_list[j] = '^' + key_list[j]
                        else:
                            key_list[j] = '_' + key_list[j]
            for j in range(len(key_list)):
                if(key_list[j][0] == '='):
                    key_list[j] = key_list[j].replace('=', '')
            print("멜로디 : ", key_list)
            key_num_list = [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
            for j in range(len(key_list)):
                for key, value in key_nums.items():
                    if(key_list[j] == key):
                        key_num_list[value] = key_num_list[value] + 1
            print("멜로디 벡터 : ", key_num_list)
            for j in range(len(key_num_list)):
                x_train.write(str(key_num_list[j]))
                if (j == len(key_num_list) - 1):
                    x_train.write('\n')
                else:
                    x_train.write(', ')
        else:
            continue
x_train.close()
y_train.close()

음계 :  K:A ['c', 'f', 'g']
음계 :  K:D ['c', 'f']
음계 :  K:G ['f']
코드 :  21
멜로디 :  ['g', 'g', 'b', '^a', 'a', 'b']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 2, 0, 1, 1, 2]
코드 :  13
멜로디 :  ['g', 'a', 'b']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 1]
코드 :  28
멜로디 :  ['a', 'a']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0]
코드 :  8
멜로디 :  ['a', 'b', 'c']
멜로디 벡터 :  [1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1]
코드 :  21
멜로디 :  ['b', 'a', 'g']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 1]
코드 :  21
멜로디 :  ['g', 'g', 'b', '^a', 'a', 'b']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 2, 0, 1, 1, 2]
코드 :  13
멜로디 :  ['g', 'a', 'b']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 1]
코드 :  28
멜로디 :  ['a', 'g']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0]
코드 :  8
멜로디 :  ['^f', 'g', 'a']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 1, 1, 0, 1, 0, 0]
코드 :  21
멜로디 :  ['g']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0]
코드 :  8
멜로디 :  ['a', '^g', 'g', 'a', 'd', '^f', 'a']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 1, 1, 1, 3, 0, 0]
코드 :  21
멜로디 :  ['b', '^a', 'a', 'b'

멜로디 :  ['g', 'd', 'b']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 1]
코드 :  0
멜로디 :  ['c', 'd', 'e']
멜로디 벡터 :  [1, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  21
멜로디 :  ['d', 'b', 'g']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 1]
코드 :  0
멜로디 :  ['a', 'b', 'c']
멜로디 벡터 :  [1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1]
코드 :  0
멜로디 :  ['e', '^f']
멜로디 벡터 :  [0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0]
코드 :  21
멜로디 :  ['g']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0]
음계 :  K:G ['f']
코드 :  21
멜로디 :  ['g', 'g']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0]
코드 :  6
멜로디 :  ['a', 'a']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0]
코드 :  21
멜로디 :  ['b', 'c', 'd', 'b', 'g']
멜로디 벡터 :  [1, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 2]
코드 :  0
멜로디 :  ['e', 'e', 'c', 'b']
멜로디 벡터 :  [1, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 1]
코드 :  28
멜로디 :  ['a', 'b', 'g']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 1]
코드 :  8
멜로디 :  ['^f', 'e', 'd']
멜로디 벡터 :  [0, 0, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0]
코드 :  21
멜로디 :  ['g', 'g']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 

멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 2]
코드 :  28
멜로디 :  ['a']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0]
코드 :  23
멜로디 :  ['g']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0]
코드 :  0
멜로디 :  ['_c', 'd', '_c', 'e', '_f', 'g']
멜로디 벡터 :  [0, 0, 1, 0, 2, 0, 0, 1, 0, 0, 0, 2]
코드 :  0
멜로디 :  ['_c', 'd', '_c']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 2]
코드 :  23
멜로디 :  ['_c', 'a']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1]
코드 :  0
멜로디 :  ['_c', 'e', 'g', 'g', 'e', '_c']
멜로디 벡터 :  [0, 0, 0, 0, 2, 0, 0, 2, 0, 0, 0, 2]
코드 :  7
멜로디 :  ['d']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0]
코드 :  23
멜로디 :  ['e', 'd']
멜로디 벡터 :  [0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  0
멜로디 :  ['_c', 'd', '_c', 'e', '_f', 'g']
멜로디 벡터 :  [0, 0, 1, 0, 2, 0, 0, 1, 0, 0, 0, 2]
코드 :  21
멜로디 :  ['g', 'a', 'g', 'g', 'g']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 4, 0, 1, 0, 0]
코드 :  28
멜로디 :  ['g', '_f', 'e']
멜로디 벡터 :  [0, 0, 0, 0, 2, 0, 0, 1, 0, 0, 0, 0]
코드 :  23
멜로디 :  ['d', '_c', 'b']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 

멜로디 벡터 :  [0, 1, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0]
코드 :  27
멜로디 :  ['e', 'd', 'e']
멜로디 벡터 :  [0, 0, 1, 0, 2, 0, 0, 0, 0, 0, 0, 0]
코드 :  34
멜로디 :  ['^f', 'e', 'd']
멜로디 벡터 :  [0, 0, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0]
코드 :  19
멜로디 :  ['^c', 'b', 'a']
멜로디 벡터 :  [0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1]
코드 :  34
멜로디 :  ['^f', 'b', 'b', 'b']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 3]
음계 :  K:Bm ['c', 'f']
코드 :  34
멜로디 :  ['^f', '^f']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0]
코드 :  14
멜로디 :  ['e', 'd']
멜로디 벡터 :  [0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  27
멜로디 :  ['^c', 'a', 'a', 'b', '^c']
멜로디 벡터 :  [0, 2, 0, 0, 0, 0, 0, 0, 0, 2, 0, 1]
코드 :  34
멜로디 :  ['d', '^c', 'b']
멜로디 벡터 :  [0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1]
코드 :  19
멜로디 :  ['^c', 'b', 'a']
멜로디 벡터 :  [0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1]
코드 :  34
멜로디 :  ['b', '^c', 'd', 'e']
멜로디 벡터 :  [0, 1, 1, 0, 1, 0, 0, 0, 0, 0, 0, 1]
코드 :  34
멜로디 :  ['^f', '^g', 'g', 'a']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 0, 0]
코드 :  19
멜로디 :  ['g', '^f', 'e']
멜로

멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 1, 2, 0, 0, 0, 0]
코드 :  20
멜로디 :  ['e', '^f', 'e']
멜로디 벡터 :  [0, 0, 0, 0, 2, 0, 1, 0, 0, 0, 0, 0]
코드 :  34
멜로디 :  ['d', 'b', 'b', 'b']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 3]
음계 :  K:D ['c', 'f']
코드 :  6
멜로디 :  ['d', 'a', '^f', 'd', '^f', 'a']
멜로디 벡터 :  [0, 0, 2, 0, 0, 0, 2, 0, 0, 2, 0, 0]
코드 :  6
멜로디 :  ['d', 'e', 'd']
멜로디 벡터 :  [0, 0, 2, 0, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  29
멜로디 :  ['^c', 'b', 'a']
멜로디 벡터 :  [0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1]
코드 :  6
멜로디 :  ['d', '^c', 'd']
멜로디 벡터 :  [0, 1, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0]
코드 :  34
멜로디 :  ['^f', 'd', '^f']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 2, 0, 0, 0, 0, 0]
코드 :  29
멜로디 :  ['e', '^c', 'a']
멜로디 벡터 :  [0, 1, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0]
코드 :  6
멜로디 :  ['d', 'a', '^f', 'd', '^f', 'a']
멜로디 벡터 :  [0, 0, 2, 0, 0, 0, 2, 0, 0, 2, 0, 0]
코드 :  6
멜로디 :  ['d', 'e', 'd']
멜로디 벡터 :  [0, 0, 2, 0, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  34
멜로디 :  ['d', '^c', 'd']
멜로디 벡터 :  [0, 1, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0]
코드 :  29
멜로디 :  ['e', 

...

코드 :  27
멜로디 :  ['e', '^f', 'e', 'e', '^f', 'g']
멜로디 벡터 :  [0, 0, 0, 0, 3, 0, 2, 1, 0, 0, 0, 0]
코드 :  6
멜로디 :  ['d', 'd']
멜로디 벡터 :  [0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0]
코드 :  12
멜로디 :  ['^c', 'd']
멜로디 벡터 :  [0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0]
코드 :  27
멜로디 :  ['e', '^c', 'a', 'a', 'a']
멜로디 벡터 :  [0, 1, 0, 0, 1, 0, 0, 0, 0, 3, 0, 0]
코드 :  6
멜로디 :  ['d', 'd', '^c', 'd']
멜로디 벡터 :  [0, 1, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0]
코드 :  27
멜로디 :  ['e', '^f', 'd', 'e', '^f', 'g']
멜로디 벡터 :  [0, 0, 1, 0, 2, 0, 2, 1, 0, 0, 0, 0]
코드 :  6
멜로디 :  ['a', '^f', 'd']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 0]
코드 :  27
멜로디 :  ['g', 'e', '^c']
멜로디 벡터 :  [0, 1, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0]
코드 :  6
멜로디 :  ['d', 'd', 'd', 'a']
멜로디 벡터 :  [0, 0, 3, 0, 0, 0, 0, 0, 0, 1, 0, 0]
코드 :  6
멜로디 :  ['d', 'd', 'd', 'e']
멜로디 벡터 :  [0, 0, 3, 0, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  6
멜로디 :  ['^f', '^f', '^f', 'd', '^f']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 4, 0, 0, 0, 0, 0]
코드 :  13
멜로디 :  ['g', 'g', 'g', 'e', 'g']
멜로디 벡터 :  [0, 0, 0, 0, 1, 0

멜로디 :  ['^f', 'a', '^f']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 2, 0, 0, 1, 0, 0]
코드 :  27
멜로디 :  ['e', 'd', '^c']
멜로디 벡터 :  [0, 1, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  34
멜로디 :  ['b', '^c', 'b']
멜로디 벡터 :  [0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2]
코드 :  12
멜로디 :  ['d', '^f']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0]
음계 :  K:C ['c', 'f', 'g']
코드 :  0
멜로디 :  ['_c', '_c']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2]
코드 :  21
멜로디 :  ['d', '_c', 'a']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 1]
코드 :  0
멜로디 :  ['_g', '_c', 'e']
멜로디 벡터 :  [0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 1]
코드 :  21
멜로디 :  ['d', 'a', '_g']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 0]
코드 :  0
멜로디 :  ['e', '_g', '_c']
멜로디 벡터 :  [0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 1]
코드 :  15
멜로디 :  ['a', '_g', '_f']
멜로디 벡터 :  [0, 0, 0, 0, 1, 0, 1, 0, 0, 1, 0, 0]
코드 :  0
멜로디 :  ['e', '_g', 'e']
멜로디 벡터 :  [0, 0, 0, 0, 2, 0, 1, 0, 0, 0, 0, 0]
코드 :  21
멜로디 :  ['d', 'e', 'd']
멜로디 벡터 :  [0, 0, 2, 0, 1, 0, 0, 0, 0, 0, 0, 0]
코드 :  0
멜로디 :  ['_c', '_c']
멜로디 벡

코드 :  27
멜로디 :  ['e', 'e']
멜로디 벡터 :  [0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0]
코드 :  12
멜로디 :  ['d', '^c', 'b']
멜로디 벡터 :  [0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1]
코드 :  27
멜로디 :  ['^c', 'a', '^g']
멜로디 벡터 :  [0, 1, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0]
코드 :  6
멜로디 :  ['a', 'd', '^f']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 0]
코드 :  27
멜로디 :  ['e', 'e']
멜로디 벡터 :  [0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0]
코드 :  6
멜로디 :  ['d', '^f', 'd']
멜로디 벡터 :  [0, 0, 2, 0, 0, 0, 1, 0, 0, 0, 0, 0]
코드 :  27
멜로디 :  ['e', '^c', 'a']
멜로디 벡터 :  [0, 1, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0]
코드 :  21
멜로디 :  ['g', '^g', 'b', 'd']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 0, 1, 1, 0, 0, 1]
코드 :  27
멜로디 :  ['e', 'e']
멜로디 벡터 :  [0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0]
코드 :  12
멜로디 :  ['d', '^c', 'b']
멜로디 벡터 :  [0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1]
코드 :  27
멜로디 :  ['^c', 'a', '^g']
멜로디 벡터 :  [0, 1, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0]
코드 :  6
멜로디 :  ['a', 'd', '^f']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 0]
코드 :  27
멜로디 :  ['e', 'a', '^c']
멜로디 벡터 :  [0, 1, 0, 0

코드 :  27
멜로디 :  ['^c', 'e', 'e', '^f', '^g', 'a', 'e', '^c']
멜로디 벡터 :  [0, 2, 0, 0, 3, 0, 1, 0, 1, 1, 0, 0]
코드 :  12
멜로디 :  ['b', 'b', 'b', 'b', 'd']
멜로디 벡터 :  [0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 4]
코드 :  27
멜로디 :  ['^c', 'a', 'e', 'a', 'a', 'e', '^c', 'a']
멜로디 벡터 :  [0, 2, 0, 0, 2, 0, 0, 0, 0, 4, 0, 0]
코드 :  12
멜로디 :  ['^c', 'e', 'b', '^c']
멜로디 벡터 :  [0, 2, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1]
코드 :  27
멜로디 :  ['a', 'a', 'a', 'a']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 0, 0]
음계 :  K:C ['c', 'f', 'g']
코드 :  28
멜로디 :  ['a', 'b', '_c', '_c', 'b', 'a']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 4]
코드 :  28
멜로디 :  ['a', 'b', '_c']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 2]
코드 :  6
멜로디 :  ['_c', 'b', 'a']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 2]
코드 :  21
멜로디 :  ['_g', '_g', '_g', '_g', 'a', 'b']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 4, 0, 0, 1, 0, 1]
코드 :  28
멜로디 :  ['a', 'b', '_c', '_c', 'b', 'a']
멜로디 벡터 :  [0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 4]
코드 :  28
멜로디 :  ['a', 'b', '_c']
멜로디 벡터 :  [0, 0, 0,

멜로디 벡터 :  [0, 0, 0, 0, 1, 0, 1, 1, 0, 1, 0, 0]
코드 :  6
멜로디 :  ['d', 'd', 'e']
멜로디 벡터 :  [0, 0, 2, 0, 1, 0, 0, 0, 0, 0, 0, 0]
